In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/README.dataset.txt
/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/README.roboflow.txt
/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/valid/armas-664-_jpg.rf.dd96d637fccae1db3e51ee740c3cbed3.jpg
/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/valid/heon_IMG_0988_JPG.rf.209da4a0d88fecf1b90ad91025a6c77d.jpg
/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/valid/traffic-light-837-_jpg.rf.2e3c1e31c070baac13b8375a0694a71b.jpg
/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/valid/16912522224892187_10_jpg.rf.d0953947971a2c1b5dcdc58fb3e4c34b.jpg
/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/valid/Cones_Video1_mp4-204_jpg.rf.0b9f7612630658a96b5faf0c0a66bab4.jpg
/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/valid/img_v2_ccf2f8dc-a986-484d-8a64-a33a4a59d78g_jpg.rf.5fe9a91148e9bb1d

In [ ]:
import cv2
import os
import json
import pandas as pd

border_size = 20
color = (0, 0, 0)

def add_border(image, border_size, color):
    bordered_image = cv2.copyMakeBorder(image, border_size, border_size, border_size, border_size, cv2.BORDER_CONSTANT, value=color)
    return bordered_image
    
def create_labels(path_in, path_out):
    # Load JSON annotation file
    json_files = [file for file in os.listdir(path_in) if file.endswith('.json')]

    with open(os.path.join(path_in, json_files[0]), 'r') as f:
        data = json.load(f)
    print(len(json_files))
    # Prepare dataframes from JSON
    df_images = pd.DataFrame(data['images'])
    df_images.rename(columns={'id': 'image_id'}, inplace=True)
    df_categories = pd.DataFrame(data['categories'])
    df_categories.rename(columns={'id': 'category_id'}, inplace=True)
    df_annotations = pd.DataFrame(data['annotations'])
    merged_df = pd.merge(df_annotations, df_categories, how='left', left_on='category_id', right_on='category_id')
    final_df = pd.merge(merged_df, df_images, how='left', left_on='image_id', right_on='image_id')

    # Prepare final dataframe for processing
    df = final_df[['category_id', 'bbox', 'file_name']]
    df[['bbox_x', 'bbox_y', 'bbox_width', 'bbox_height']] = pd.DataFrame(df['bbox'].apply(lambda x: pd.Series(x)))
    df=df.drop('bbox', axis=1)
    df=df.drop_duplicates()
    lables_folder_path='/kaggle/working/'+path_out+'/labels'
    #os.mkdir('/kaggle/working/'+path_out,)
    os.makedirs(lables_folder_path,exist_ok =True)
    for file in df['file_name'].unique():
        boxes=df[df['file_name']==file]
        lablel_path='/kaggle/working/'+path_out+'/labels/'+file[:-4]+'.txt'
        with open(lablel_path, 'a') as label_file:
            for id,box in boxes.iterrows():
                class_index = box['category_id']
                x_center = (box['bbox_x'] + box['bbox_width'] / 2 + 10) / 320
                y_center = (box['bbox_y'] + box['bbox_height'] / 2 + 10) / 320
                width = box['bbox_width'] / 320
                height = box['bbox_height'] / 320
                label_file.write(f"{class_index} {x_center} {y_center} {width} {height}\n")
    
    return df

In [3]:
import shutil
def fill_folders(images,folder):
    folder_path='/kaggle/working/'+folder+'/images/'
    #os.mkdir('/kaggle/working/'+path_out,)
    os.makedirs(folder_path,exist_ok =True)
    for image in images:
        #os.rename('/kaggle/input/cars-video-object-tracking/images/'+image,'/kaggle/working/'+folder+'/images/'+image)
        shutil.copyfile('/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/'+folder+'/'+image,folder_path+image)


In [4]:
train = [file for file in os.listdir('/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/train') if not file.endswith('.json')]
test = [file for file in os.listdir('/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/test') if not file.endswith('.json')]
val = [file for file in os.listdir('/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/valid') if not file.endswith('.json')]

In [5]:
fill_folders(train,'train')
fill_folders(test,'test')
fill_folders(val,'valid')

In [6]:
import yaml
yaml_file_path='/kaggle/working/data.yaml'
train_data = {
      'train':'/kaggle/working/train/images',
      'val':'/kaggle/working/valid/images',
      'test':'/kaggle/working/test/images',
      'names': [
        'cars-bikes-people', 'Bus', 'Bushes', 'Person', 'Truck', 'backpack', 'bench',
        'bicycle', 'boat', 'branch', 'car', 'chair', 'clock', 'crosswalk', 'door',
        'elevator', 'fire_hydrant', 'green_light', 'gun', 'handbag', 'motorcycle',
        'person', 'pothole', 'rat', 'red_light', 'scooter', 'sheep', 'stairs', 'stop_sign',
        'suitcase', 'traffic light', 'traffic_cone', 'train', 'tree', 'truck', 'umbrella',
        'yellow_light'
        ]
     }


print(yaml.dump(train_data))
with open(yaml_file_path, "w") as outfile:
    yaml.dump(train_data, outfile, default_flow_style=False)

names:
- cars-bikes-people
- Bus
- Bushes
- Person
- Truck
- backpack
- bench
- bicycle
- boat
- branch
- car
- chair
- clock
- crosswalk
- door
- elevator
- fire_hydrant
- green_light
- gun
- handbag
- motorcycle
- person
- pothole
- rat
- red_light
- scooter
- sheep
- stairs
- stop_sign
- suitcase
- traffic light
- traffic_cone
- train
- tree
- truck
- umbrella
- yellow_light
test: /kaggle/working/test/images
train: /kaggle/working/train/images
val: /kaggle/working/valid/images



In [7]:
df=create_labels('/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/train','train')
df=create_labels('/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/test','test')
df=create_labels('/kaggle/input/26-class-object-detection-dataset/Senior-Design-VIAD-4/valid','valid')


1


/tmp/ipykernel_35/780571746.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[['bbox_x', 'bbox_y', 'bbox_width', 'bbox_height']] = pd.DataFrame(df['bbox'].apply(lambda x: pd.Series(x)))
/tmp/ipykernel_35/780571746.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[['bbox_x', 'bbox_y', 'bbox_width', 'bbox_height']] = pd.DataFrame(df['bbox'].apply(lambda x: pd.Series(x)))
/tmp/ipykernel_35/780571746.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
T

1


/tmp/ipykernel_35/780571746.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[['bbox_x', 'bbox_y', 'bbox_width', 'bbox_height']] = pd.DataFrame(df['bbox'].apply(lambda x: pd.Series(x)))
/tmp/ipykernel_35/780571746.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[['bbox_x', 'bbox_y', 'bbox_width', 'bbox_height']] = pd.DataFrame(df['bbox'].apply(lambda x: pd.Series(x)))
/tmp/ipykernel_35/780571746.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
T

1


/tmp/ipykernel_35/780571746.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[['bbox_x', 'bbox_y', 'bbox_width', 'bbox_height']] = pd.DataFrame(df['bbox'].apply(lambda x: pd.Series(x)))
/tmp/ipykernel_35/780571746.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[['bbox_x', 'bbox_y', 'bbox_width', 'bbox_height']] = pd.DataFrame(df['bbox'].apply(lambda x: pd.Series(x)))
/tmp/ipykernel_35/780571746.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
T

In [8]:
!pip install ultralytics


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 16.9 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.7 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.4 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 8.0 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 31.1 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 13.8 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 8.2 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 77.0 MB/s eta 0:00:00:00:0100:01
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.9.41
    Uninstalling nvidia-nvjitlink-cu12-12.9.41:
      Successfully uninstalled nvidia-nvjitlink-cu12-12.9.41
  Attempting uninstall: nvidia-curand-cu12
    Found exi

In [9]:
from ultralytics import YOLO

Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


In [ ]:
model = YOLO("yolo11s.pt") 
results = model.train(data=yaml_file_path, epochs=30, imgsz=640, device=[0, 1])

100%|██████████| 18.4M/18.4M [00:00<00:00, 153MB/s]


Ultralytics 8.3.153 🚀 Python-3.11.11 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
                                                        CUDA:1 (Tesla T4, 15095MiB)
engine/trainer: agnostic_nms=False, amp=True, augment=False, auto_augment=randaugment, batch=16, bgr=0.0, box=7.5, cache=False, cfg=None, classes=None, close_mosaic=10, cls=0.5, conf=None, copy_paste=0.0, copy_paste_mode=flip, cos_lr=False, cutmix=0.0, data=/kaggle/working/data.yaml, degrees=0.0, deterministic=True, device=0,1, dfl=1.5, dnn=False, dropout=0.0, dynamic=False, embed=None, epochs=30, erasing=0.4, exist_ok=False, fliplr=0.5, flipud=0.0, format=torchscript, fraction=1.0, freeze=None, half=False, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, imgsz=640, int8=False, iou=0.7, keras=False, kobj=1.0, line_width=None, lr0=0.01, lrf=0.01, mask_ratio=4, max_det=300, mixup=0.0, mode=train, model=yolo11s.pt, momentum=0.937, mosaic=1.0, multi_scale=False, name=train, nbs=64, nms=False, opset=None, optimize=False, optimizer=auto, ove

100%|██████████| 755k/755k [00:00<00:00, 17.1MB/s]


Overriding model.yaml nc=80 with nc=37

                   from  n    params  module                                       arguments                     
  0                  -1  1       928  ultralytics.nn.modules.conv.Conv             [3, 32, 3, 2]                 
  1                  -1  1     18560  ultralytics.nn.modules.conv.Conv             [32, 64, 3, 2]                
  2                  -1  1     26080  ultralytics.nn.modules.block.C3k2            [64, 128, 1, False, 0.25]     
  3                  -1  1    147712  ultralytics.nn.modules.conv.Conv             [128, 128, 3, 2]              
  4                  -1  1    103360  ultralytics.nn.modules.block.C3k2            [128, 256, 1, False, 0.25]    
  5                  -1  1    590336  ultralytics.nn.modules.conv.Conv             [256, 256, 3, 2]              
  6                  -1  1    346112  ultralytics.nn.modules.block.C3k2            [256, 256, 1, True]           
  7                  -1  1   1180672  ultralytic

100%|██████████| 5.35M/5.35M [00:00<00:00, 70.3MB/s]


...

      22/30      3.92G      0.999     0.7434      1.269         12        640: 100%|██████████| 2032/2032 [06:05<00:00,  5.55it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 266/266 [00:37<00:00,  7.10it/s]


                   all       4246       7242      0.666      0.484      0.513      0.352

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


      23/30      3.95G      0.971     0.7163      1.255         40        640: 100%|██████████| 2032/2032 [06:07<00:00,  5.53it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 266/266 [00:37<00:00,  7.10it/s]


                   all       4246       7242      0.664      0.483      0.515      0.355

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


      24/30      3.97G     0.8727     0.6558      1.194         12        640:   2%|▏         | 42/2032 [00:07<05:39,  5.86it/s]